In [1]:
import pandas as pd
mydb=pd.read_csv('Data for ML/new_dB_for_ML_restructured.csv')
#print (mydb.count())
newdb=mydb.drop(mydb.columns[0], axis=1)
newdb.head()

import numpy as np
allcolumns=newdb.columns
myXcolumns=[s for s in allcolumns if '0_section' in s and '_travel time' not in s]
myXcolumns.extend(['p1','p2','p3','p4','p5','p6','p7','p8','p9','p10','p11','p12','p13','p14','p15','p16'])
#print (3*72+16)
myYcolumns=[s for s in allcolumns if '0_section' in s and '_travel time' in s]
print (len(myXcolumns))
print (len(myYcolumns))
#from sklearn.linear_model import LinearRegression
#print (myXcolumns)
X=np.array(newdb[myXcolumns])
X_df=newdb[myXcolumns]
#X = X.transpose()
y=np.array(sum(newdb[i] for i in myYcolumns))

#y = y.transpose()
#y=y.reshape(len(y),1)
from sklearn import preprocessing
lab_enc = preprocessing.LabelEncoder()
y = lab_enc.fit_transform(y)

print (X.shape)
print (y.shape)
X

232
72
(9743, 232)
(9743,)


array([[138.  ,  31.41,  96.56, ...,   0.  ,   1.  ,   1.  ],
       [138.  ,  31.41,  96.56, ...,   0.  ,   1.  ,   1.  ],
       [138.  ,  31.18,  96.6 , ...,   0.  ,   1.  ,   1.  ],
       ...,
       [798.  ,  40.55,  15.64, ...,  13.  ,   3.  ,  15.  ],
       [768.  ,  40.06,  17.61, ...,  14.  ,   3.  ,  15.  ],
       [768.  ,  40.06,  17.61, ...,  14.  ,   3.  ,  15.  ]])

In [2]:
import csv
import sys, os, errno
import os.path
import io
import pdb
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.pylab import rcParams
import pprint
from sklearn import linear_model
from sklearn.model_selection import cross_val_score, cross_validate, cross_val_predict, LeaveOneOut, KFold, StratifiedKFold
from sklearn.metrics import recall_score, accuracy_score, precision_score,f1_score, make_scorer
from sklearn import metrics   
from sklearn.model_selection import GridSearchCV,RandomizedSearchCV
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split, KFold, LeaveOneOut
from sklearn import neighbors
from sklearn import preprocessing # for standardization
from sklearn.ensemble import GradientBoostingRegressor
import xgboost as xgb
from xgboost import XGBClassifier, XGBRegressor, plot_tree, plot_importance
# Additional modules
from time import time
from scipy.stats import randint as sp_randint
import multiprocessing
from scipy.stats import randint as sp_randint
import copy
#from prepros import preprocessor, preprocessor_modified_stem, preprocessor_modified_noStem
from sklearn.preprocessing import FunctionTransformer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.pipeline import Pipeline, FeatureUnion, make_pipeline, make_union
from sklearn.feature_extraction.text import TfidfTransformer
import nltk
import dill
import re
from nltk.stem.snowball import SnowballStemmer
import sklearn, nltk, scipy
from nltk.corpus import stopwords
from scipy.stats import kendalltau, spearmanr, pearsonr

print('The nltk version is {}.'.format(nltk.__version__))
print('The scikit-learn version is {}.'.format(sklearn.__version__))
print('The scipy version is {}.'.format(scipy.__version__))

from datetime import datetime
print('Executed at {}'.format(str(datetime.now())))
### core function for mape calculation
def mean_absolute_percentage_error_func(y_true, y_pred): 
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    y_true = y_true[np.nonzero(y_true)] # avoid incidents with zero duration
    y_pred = y_pred[np.nonzero(y_true)]
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

def mean_absolute_percentage_error_log_func(y_true, y_pred):
    # input in Log
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    y_true = np.expm1(y_true); y_pred = np.expm1(y_pred)
    y_true = y_true[np.nonzero(y_true)] # avoid incidents with zero duration
    y_pred = y_pred[np.nonzero(y_true)]
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

def spearman_func(y_true, y_pred):
    '''
    Optimize the hyperparameter values during the grid search based on
    Spearman rank correlation.

    This is useful in cases where you want to use the actual probabilities of
    the different classes after the fact, and not just the optimize based on
    the classification accuracy.
    '''
    ret_score = spearmanr(y_true, y_pred)[0]
    return ret_score if not np.isnan(ret_score) else 0.0

def pearson_func(y_true, y_pred):
    '''
    Optimize the hyperparameter values during the grid search based on Pearson
    correlation.
    '''
    ret_score = pearsonr(y_true, y_pred)[0]
    return ret_score if not np.isnan(ret_score) else 0.0

# Utility function to report best scores
def report(results, n_top=3):
    for i in range(1, n_top + 1):
        candidates = np.flatnonzero(results['rank_test_score'] == i)
        for candidate in candidates:
            print("Model with rank: {0}".format(i))
            print("Mean validation score: {0:.3f} (std: {1:.3f})".format(
                  results['mean_test_score'][candidate],
                  results['std_test_score'][candidate]))
            print("Parameters: {0}".format(results['params'][candidate]))
            print("")

# #  Resources for NLP BoW
# ## Stemmer
# stemmer = SnowballStemmer("english")
# stopwords_en = set(stopwords.words('english'))

# ## now build a custom tokenizer based on these
# __tokenization_pattern = r'''(?x)          # set flag to allow verbose regexps
#         \$?\d+(?:\.\d+)?%?  # currency and percentages, e.g. $12.40, 82%
#       | (?:[A-Z]\.)+        # abbreviations, e.g. U.S.A.
#       | \w+(?:-\w+)*        # words with optional internal hyphens
#       | \.\.\.              # ellipsis
#       | [][.,;"'?():_`-]    # these are separate tokens; includes ], [
#     '''

# tokenizer = nltk.tokenize.regexp.RegexpTokenizer(__tokenization_pattern)

print('Executed at {}'.format(str(datetime.now())))

The nltk version is 3.4.
The scikit-learn version is 0.20.3.
The scipy version is 1.2.1.
Executed at 2019-11-11 00:34:17.431280
Executed at 2019-11-11 00:34:17.431280


In [3]:
Y=y

In [4]:
# parameters and ranges to plot
param_test11 = {
    'learning_rate' : [0.0001, 0.001, 0.1], 
    'n_estimators' : range(20,200,1),
    'max_depth':range(3,16,2), 
    'subsample':[0.6,0.7,0.75,0.8,0.85,0.9,0.95,1.0]
}

# for RF
param_test21 = {
#     'learning_rate' : [0.0001, 0.001, 0.1],  # RF does not have such param
    'n_estimators' : range(20,200,1),
    'max_depth':range(3,16,2) 
#     'subsample':[0.6,0.7,0.75,0.8,0.85,0.9,0.95,1.0]  # RF does not have such param
}

n_iter_search = 200

gbt02 = GradientBoostingRegressor (verbose = 0)
xgb000 = XGBRegressor()
rf000 = RandomForestRegressor(verbose = 0)

scorers = {'mape':make_scorer(mean_absolute_percentage_error_func, greater_is_better=False)}
scorers['r2'] = 'r2'
scorers['neg_mean_squared_error'] = 'neg_mean_squared_error'
scorers['pearson'] = make_scorer(pearson_func, greater_is_better=True)
scorers['spearman'] = make_scorer(spearman_func, greater_is_better=True)

print('Scorers used for evaluation: {}'.format(scorers))

print('Executed at {}'.format(str(datetime.now())))

Scorers used for evaluation: {'mape': make_scorer(mean_absolute_percentage_error_func, greater_is_better=False), 'r2': 'r2', 'neg_mean_squared_error': 'neg_mean_squared_error', 'pearson': make_scorer(pearson_func), 'spearman': make_scorer(spearman_func)}
Executed at 2019-11-11 00:34:17.471173


In [5]:
# best regressors and parameters

bestparameter={
    'objective':'reg:squarederror',
     'learning_rate' : 0.6, 
    'n_estimators' : 190,
    'max_depth':7, 
    'subsample':0.8,
    'n_jobs':1
}

#sample code
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=123)
#bestregressor = xgb.XGBRegressor(**bestparameter)
#manually import the best regressor
bestregressor = xgb.XGBRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
             colsample_bynode=1, colsample_bytree=1, gamma=0,
             importance_type='gain', learning_rate=0.1, max_delta_step=0,
             max_depth=7, min_child_weight=1, missing=None, n_estimators=190,
             n_jobs=1, nthread=None, objective='reg:linear', random_state=0,
             reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
             silent=None, subsample=0.6, verbosity=1)

In [6]:
#load regressor from external file

#bestregressor.load_model('mybest_model')
print (bestregressor)
#ready to predict

#bestregressor.predict(new_x)

XGBRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bynode=1, colsample_bytree=1, gamma=0,
       importance_type='gain', learning_rate=0.1, max_delta_step=0,
       max_depth=7, min_child_weight=1, missing=None, n_estimators=190,
       n_jobs=1, nthread=None, objective='reg:linear', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
       silent=None, subsample=0.6, verbosity=1)


In [7]:
bestregressor.fit(X_train, y_train,
                  verbose=True,
                  eval_set=[(X_train,y_train)],
                  #eval_metric=scorers['mape']
                 )
preds=bestregressor.predict(X_test)
import sklearn.metrics as met
rmse=np.sqrt(met.mean_squared_error(y_test, preds))
print("RMSE: %f" % (rmse))
evals_result = bestregressor.evals_result()
print (evals_result)
bestregressor.save_model('mybest_model')
print('Executed at {}'.format(str(datetime.now())))

[00:34:17] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[0]	validation_0-rmse:4949.2
[1]	validation_0-rmse:4492.9
[2]	validation_0-rmse:4082.03
[3]	validation_0-rmse:3711.92
[4]	validation_0-rmse:3380.16
[5]	validation_0-rmse:3077.48
[6]	validation_0-rmse:2811.5
[7]	validation_0-rmse:2565.39
[8]	validation_0-rmse:2349.72
[9]	validation_0-rmse:2151.73
[10]	validation_0-rmse:1970.77
[11]	validation_0-rmse:1806.75
[12]	validation_0-rmse:1664.3
[13]	validation_0-rmse:1532.87
[14]	validation_0-rmse:1416.72
[15]	validation_0-rmse:1313.85
[16]	validation_0-rmse:1218.96
[17]	validation_0-rmse:1131.08
[18]	validation_0-rmse:1054.44
[19]	validation_0-rmse:982.924
[20]	validation_0-rmse:918.29
[21]	validation_0-rmse:863.444
[22]	validation_0-rmse:811.106
[23]	validation_0-rmse:766.543
[24]	validation_0-rmse:725.271
[25]	validation_0-rmse:685.175
[26]	validation_0-rmse:648.57
[27]	validation

In [8]:
#preds=bestregressor.predict([X_test[0]])


In [9]:
#preds

In [10]:
#[X_test[0]]

In [11]:
#GA part
# SITEPACKAGES= "C:\\Program Files\\Aimsun\\Aimsun Next 8.2\\Lib\\site-packages"
# if SITEPACKAGES not in sys.path:
# 	sys.path.append(SITEPACKAGES)
import pandas as pd
import numpy as np
import time
import random

In [12]:
#step 1 output data directly into dataframes

import os.path as osp
#folder_path = r"C:\Users\mao010\Desktop\tmp\GA experiment\output\four_intersection"
folder_path = r"Data for GA"
file_name_1 = 'intersection.csv'
file_name_2 = 'phase.csv'
file_name_3 = 'link.csv'

# #step 1.1 intersection table
# file_path = osp.join(folder_path, file_name_1)
# file = open(file_path, "w")
# file.write("IntersectionID,NumOfPhase,CycleTime\n")
# control_plan=model.getCatalog().find(1068)
# junctions=control_plan.getControlJunctions()
# for junction in junctions:
# 	#print junction
# 	junctionNode=model.getCatalog().find(junction)
# 	controljunction=control_plan.getControlJunction(junctionNode)
# 	cycle=controljunction.getCycle()
# 	phases=controljunction.getPhases()
# 	if len(phases)>0:
# 		file.write("%i,%i,%i\n"%(junction,len(phases),cycle))
# file.close()
# #step 1.2 phase table
# file_path = osp.join(folder_path, file_name_2)
# file = open(file_path, "w")
# file.write("IntersectionID,phaseID,PhaseDuration,GreenLinkID\n")
# control_plan=model.getCatalog().find(1068)
# junctions=control_plan.getControlJunctions()

# for junction in junctions:
# 	#print junction
# 	myphaseID=1
# 	junctionNode=model.getCatalog().find(junction)
# 	controljunction=control_plan.getControlJunction(junctionNode)
# 	cycle=controljunction.getCycle()
# 	phases=controljunction.getPhases()
# 	allturnings=junctionNode.getTurnings()
# 	for each_phase in phases:
# 		duration=each_phase.getDuration()
# 		file.write("%i," %junction)
# 		file.write("%i," %myphaseID)
# 		file.write("%i," %duration)
# 		myphaseID+=1
# 		for each_turning in allturnings:
# 			if each_phase.turningHasGreen(each_turning)==1:
# 				#print str("this phase consist turining:"+str(each_turning.getId()))
# 				myoriginsection=each_turning.getOrigin()
# 				mysectionID=myoriginsection.getId()
# 				file.write("_%i" %mysectionID)
# 		file.write("\n")
# file.close()
# #step 1.3 link table
# #link table
# file_path = osp.join(folder_path, file_name_3)
# file = open(file_path, "w")
# file.write("linkID,length,speedlimit,capacity,fromNodeId,toNodeId,cost,linkgreensplit,flow\n")
# sectionType = model.getType( "GKSection" )
# for section in model.getCatalog().getObjectsByType( sectionType ).itervalues():
# 	file.write("%i,%2f,"%(section.getId(),section.getLanesLength()))
# 	if section.getOrigin()==None:
# 		file.write("%i,%2f,%i,%i,%2f,%2f,%f" %(section.getSpeed(),section.getCapacity(),-1,section.getDestination().getId(),section.getUserDefinedCost2(),section.getUserDefinedCost(),0))
# 	elif section.getDestination()==None:
# 		file.write("%i,%2f,%i,%i,%2f,%2f,%f" %(section.getSpeed(),section.getCapacity(),section.getOrigin().getId(),-1,section.getUserDefinedCost2(),section.getUserDefinedCost(),0))
# 	else:
# 		file.write("%i,%2f,%i,%i,%2f,%2f,%f" %(section.getSpeed(),section.getCapacity(),section.getOrigin().getId(),section.getDestination().getId(),section.getUserDefinedCost2(),section.getUserDefinedCost(),0))
# 	file.write("\n")

# file.close()
#step 1.4 read all tables and turn into dataframes
#Table1 =pd.read_csv('C:\\Users\\mao010\\Desktop\\tmp\\GA experiment\\output\\four_intersection\\ntersection.csv')
Table1 =pd.read_csv(osp.join(folder_path, file_name_1))
Table1.columns=['IntersectionID','NumOfPhase','CycleTime']

#print Table1

#Table2 =pd.read_csv('C:\\Users\\mao010\\Desktop\\tmp\\GA experiment\\output\\four_intersection\\phase.csv')
Table2 =pd.read_csv(osp.join(folder_path, file_name_2))
Table2.columns=['IntersectionID','PhaseID','PhaseDuration','GreenLinkID']

#print Table2

#Table3 =pd.read_csv('C:\\Users\\mao010\\Desktop\\tmp\\GA experiment\\output\\four_intersection\\link.csv')
#print Table3
Table3 =pd.read_csv(osp.join(folder_path, file_name_3))

In [13]:
"""
signal optimization
"""
class OptimizeSignal():
	def __init__(self, filepointer,limit, size,intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,prob_crossover=0.9, prob_mutation=0.1):
		#self.target = (phaseTB['PhaseDuration']).copy()
		self.counter = 0
		self.filepath=filepointer
		self.limit = limit#genreation limit
		self.size = size#population size
		self.prob_crossover = prob_crossover
		self.prob_mutation = prob_mutation
		self.intersectionTB=intersectionTB
		self.phaseTB=phaseTB
		self.linkTB=linkTB
		pass
	
	#GA main body
	def run(self,intersectionTB,phaseTB,linkTB):
		#print ("step 1 initial")
		population = self.initial(intersectionTB,phaseTB,linkTB)
		while True:
			
#			fits_pops = [(self.fitness(ch,intersectionTB,phaseTB,linkTB),  ch) for ch in population]
			fits_pops = [(self.fitness_GA_ML(ch,intersectionTB,phaseTB,linkTB),  ch) for ch in population]            
			if self.check_stop(fits_pops): break
			population = self.next(fits_pops)
			pass
		return population

	def next(self, fits):
		#print ("step 2 generate next generation")
		parents_generator = self.parents(fits)
		size = len(fits)
		nexts = []
		while len(nexts) < size:
			parents = next(parents_generator)
			cross = random.random() < self.probability_crossover()
			children = self.crossover(parents) if cross else parents
			for ch in children:
				mutate = random.random() < self.probability_mutation()
				#nexts.append(self.mutation_reinforced(ch) if mutate else ch)
				nexts.append(self.mutation(ch) if mutate else ch)
				pass
			pass
		#print ("finished generate one generation")
		#print (nexts)
		return nexts[0:size]
	pass
	# GeneticFunctions interface impls
	def probability_crossover(self):
		return self.prob_crossover

	def probability_mutation(self):
		return self.prob_mutation

	def initial(self,intersectionTB,phaseTB,linkTB):
		return [self.random_chromo(intersectionTB,phaseTB,linkTB) for j in range(self.size)]

	def fitness(self, chromo,intersectionTB,phaseTB,linkTB):
		# larger is better
		#fitness=self.costfunction(chromo,phaseTB,linkTB,intersectionTB) # for approach 1, we use calculation to get cost
		#for approach 2, we use simulation results as cost
		#update signal settings
		print (chromo)
		self.updateSignals(chromo,phaseTB)
		self.update_link_green_split_AIMSUN()
		fitness=-self.get_simulated_cost()
		return fitness
    #this is the new fitness value generated by the ML module.
	def fitness_GA_ML(self, chromo,intersectionTB,phaseTB,linkTB):
		# larger is better
        
        #maybe we need to push some status of the links
        
        ######
		print (chromo)

		fitness=-self.get_ML_predicted_cost(chromo)
		return fitness

	def check_stop(self, fits_pops):
		self.counter += 1
		myfitlist=[]
		#mychromo=[]
		#myfile2=open(r"C:\Users\mao010\Desktop\tmp\GA experiment\output\four_intersection\GAoutput_detail.csv","a")
		myfile2=open("output\GAoutput_detail.csv","a")
		myfile2.write("generation ID:,"+str(self.counter)+"\n")
		for i in range(len(fits_pops)):
			myfit,a=fits_pops[i]
			myfitlist.append(myfit)
			#mychromo.append([a])
			myfile2.write("GenerationID,%i,fitness,%f,[a,b,c,d]," %(self.counter,myfit))
			for i in range(len(a)):
				myfile2.write("%s,"%a[i])
			myfile2.write("\n")
		std=np.std(myfitlist)
		max=np.amax(myfitlist)
		min=np.amin(myfitlist)
		mean=np.mean(myfitlist)
		print (self.filepath)
		myfile=open(str(self.filepath),"a") 
		myfile.write("%i,%f,%f,%f,%f,%s\n" %(self.counter,max,min,mean,std,str(time.ctime())))
		myfile.close()
		
		#myfile2.write(fits_pops)
		#fits_pops.to_csv(r"C:\Users\mao010\Desktop\tmp\GA experiment\output\GAoutput_detail.csv",index=True)
		myfile2.write("\n")
		
		if self.counter >= self.limit:
			for i in range(len(fits_pops)):
				myfit,a=fits_pops[i]
				if i ==0:
					largest_fitness=myfit
					best_signal=a
				else:
					if myfit>largest_fitness:
						largest_fitness=myfit
						best_signal=a
			print ("current iteration: best fitness is:")
			print (largest_fitness)
			print ("signal setting:")
			print (best_signal)
		if self.counter <= self.limit:
			for i in range(len(fits_pops)):
				myfit,a=fits_pops[i]
				if i ==0:
					largest_fitness=myfit
					best_signal=a
				else:
					if myfit>largest_fitness:
						largest_fitness=myfit
						best_signal=a
			myfile2.write("current iteration: best fitness is:, %f,signal setting:,%s\n"%(largest_fitness,str(best_signal)))
		myfile2.close()
		return self.counter >= self.limit

	def parents(self, fits_populations):
		while True:
			father = self.tournament(fits_populations,self.phaseTB,self.linkTB,self.intersectionTB)
			mother = self.tournament(fits_populations,self.phaseTB,self.linkTB,self.intersectionTB)
			
			yield (father, mother)
			pass
		pass

  
	#cross over function #Need two parents and generate two children
	def crossover(self, parents):
		father, mother = parents
		#Need to truncate father,mother into one intersection(four phase)
		index1 = random.random()
		index2 = random.random()
		child1=list()
		child2=list()
		while index2==index1:
			index2 = random.random()
		if len(father)==len(self.phaseTB.index):
			pass
		else:
			print ("father, mather have wrong number of phaes!")
		linecounter=0
		for index,row in self.intersectionTB.iterrows():
			subfather=list()
			submother=list()
			
			cycleleftmother=row['CycleTime']
			cycleleftfather=row['CycleTime']
			numofphases=row['NumOfPhase']
			for i in range(numofphases):
				subfather.append(father[linecounter])
				submother.append(mother[linecounter])
				linecounter+=1
			
			#print(cycleleft1)
			#print(cycleleft2)
			for i in range(len(subfather)):
				if i !=len(subfather)-1:
					child1.append(int(index1*subfather[i] + (1-index1)*submother[i]))
					child2.append(int(index2*subfather[i] + (1-index2)*submother[i]))
					cycleleftfather=cycleleftfather-int(index1*subfather[i] + (1-index1)*submother[i])
					cycleleftmother=cycleleftmother-int(index2*subfather[i] + (1-index2)*submother[i])
				else:
					child1.append(cycleleftfather)
					child2.append(cycleleftmother)
		return (child1, child2)

	def mutation(self, chromosome):
		#Need to truncate father,mother into one intersection(four phase)
		linecounter=0
		newchromosome=list()
		for index,row in self.intersectionTB.iterrows():
			subchromo=list()
			numofphases=row['NumOfPhase']
			for i in range(numofphases):
				subchromo.append(chromosome[linecounter])
				linecounter+=1
			id1=random.randint(0,len(subchromo)-1)
			id2=random.randint(0,len(subchromo)-1)
			while id1==id2:
				id2=random.randint(0,len(subchromo)-1)
			#print (id1,id2)
			
			if subchromo[id1]==0:
				vary=0
			else:
				vary=random.randint(1,subchromo[id1])
			#print (vary)
			for i in range(len(subchromo)):
				if i == id1:
					newchromosome.append(subchromo[i]-vary)
				elif i == id2:
					newchromosome.append(subchromo[i]+vary)
				else:
					newchromosome.append(subchromo[i])
		return newchromosome
	def mutation_reinforced(self, chromosome):
		#Need to truncate father,mother into one intersection(four phase)
		if mytb.loc[mytb['state']==str([chromosome])].empty:
			linecounter=0
			newchromosome=list()
			for index,row in self.intersectionTB.iterrows():
				subchromo=list()
				numofphases=row['NumOfPhase']
				for i in range(numofphases):
					subchromo.append(chromosome[linecounter])
					linecounter+=1
				id1=random.randint(0,len(subchromo)-1)
				id2=random.randint(0,len(subchromo)-1)
				while id1==id2:
					id2=random.randint(0,len(subchromo)-1)
				#print (id1,id2)
				
				if subchromo[id1]==0:
					vary=0
				else:
					vary=random.randint(1,subchromo[id1])
				#print (vary)
				for i in range(len(subchromo)):
					if i == id1:
						newchromosome.append(subchromo[i]-vary)
					elif i == id2:
						newchromosome.append(subchromo[i]+vary)
					else:
						newchromosome.append(subchromo[i])
			return newchromosome
		else:
			new1=r_table.loc[r_table["state"]==str([s]),['action']]
			index=r_table.loc[r_table["state"]==str([s]),['action']].index[0]
			print (index)
			print ("?!?")
			###actionarray is string now,need to transfer into array
			new2=new1.reset_index()
			print ("ccc")
			print (new2.count)
			if new2['action'].count()>1:
				print ("more than one line observed with same state")
			elif new2['action'].count()==1:
				actionarray=new2.at[0,'action']
			else:
				print ("wtf")
			print (actionarray)
			max_reward=max(actionarray)
			max_reward_actionID=actionarray.index(max_reward)
			intID,id1,id2=fromID_to_action(max_reward_actionID)
			linecounter=0
			newchromosome=list()
			for index,row in self.intersectionTB.iterrows():
				subchromo=list()
				numofphases=row['NumOfPhase']
				for i in range(numofphases):
					subchromo.append(chromosome[linecounter])
					linecounter+=1
				if row['IntersectionID']==intID:
					vary=random.randint(1,subchromo[id1])
				for i in range(len(subchromo)):
					if i == id1:
						newchromosome.append(subchromo[i]-vary)
					elif i == id2:
						newchromosome.append(subchromo[i]+vary)
					else:
						newchromosome.append(subchromo[i])
				for i in range(len(subchromo)):
					if i == id1:
						newchromosome.append(subchromo[i]-vary)
					elif i == id2:
						newchromosome.append(subchromo[i]+vary)
					else:
						newchromosome.append(subchromo[i])
			return newchromosome
	def mutation_action_record(self, chromosome):
		#Need to truncate father,mother into one intersection(four phase)
		linecounter=0
		newchromosome=list()
		#print "222"
		row=intersectionTB.loc[random.randint(0,len(intersectionTB)-1)]
		#print row
		intersectionID=row['IntersectionID']
		print (intersectionID)
		for index,row in self.intersectionTB.iterrows():
			subchromo=list()
			numofphases=row['NumOfPhase']
			if row['IntersectionID']!=intersectionID:
				for i in range(numofphases):
					newchromosome.append(chromosome[linecounter])
					linecounter+=1
				continue
			
			for i in range(numofphases):
				subchromo.append(chromosome[linecounter])
				linecounter+=1
			id1=random.randint(0,len(subchromo)-1)
			id2=random.randint(0,len(subchromo)-1)
			while id1==id2 or subchromo[id1]==0:
				id1=random.randint(0,len(subchromo)-1)
				id2=random.randint(0,len(subchromo)-1)
			#print (id1,id2)
			
			if subchromo[id1]==0:
				vary=0
			else:
				vary=1#random.randint(1,subchromo[id1])
			#print (vary)
			for i in range(len(subchromo)):
				if i == id1:
					newchromosome.append(subchromo[i]-vary)
				elif i == id2:
					newchromosome.append(subchromo[i]+vary)
				else:
					newchromosome.append(subchromo[i])
		return intersectionID,id1,id2,newchromosome
	# internals
	def tournament(self,fit_population,phaseTable,linkTable,intersectionTable):
		#print ("tournament")
		#method 1: calculate cost each time called tournament
		#ice = self.select_random(fit_population)
		#ob = self.select_random(fit_population)
		#ostofalice=self.costfunction(alice,phaseTable,linkTable,intersectionTable)
		#ostofbob=self.costfunction(bob,phaseTable,linkTable,intersectionTable)
		#eturn alice if costofalice > costofbob else bob
		
		#method 2: use the dictionary prepared before
		alicef, alice = self.select_random(fit_population)
		bobf, bob = self.select_random(fit_population)
		return alice if alicef > bobf else bob

	def select_random(self, population):
		#print ("select random")
		return population[random.randint(0, len(population)-1)]

	def random_chromo(self,intersectionTB,phaseTB,linkTB):
		#target_opt=self.target
		
		chromesome1=[]#use array to store the fits population
		size=1
		for j in range(size):
			lineID=0
			arrayofchrome=list()
			#ramdom chrome
			for index,row in intersectionTB.iterrows():
				#print(row['CycleTime'])
				cycle=int(row['CycleTime'])
				cycle_time_left=cycle
				nophase=row['NumOfPhase']
				#print (nophase)
				for i in range(nophase):#i from 0 to nophase-1
					if i != (nophase-1):
						phaseduration=random.randint(0,cycle_time_left)#Return a random integer N such that a <= N <= b.
						#print (phaseduration)
						cycle_time_left=cycle_time_left-phaseduration
						#target_opt[lineID]=phaseduration
						arrayofchrome.append(phaseduration)
					else:
						#target_opt[lineID]=cycle_time_left
						arrayofchrome.append(cycle_time_left)
						#print cycle_time_left
					lineID=lineID+1
			#print (arrayofchrome)

			#chromesome1.append(arrayofchrome)


		return (arrayofchrome)
	
	def getlinkGreenSplit(self,linkTable,phaseTable,intersectionTable):
		for index,row in phaseTable.iterrows():
			greentime =int(row['PhaseDuration'])
			interID=int(row['IntersectionID'])

			for index2,row2 in intersectionTable.iterrows():
					if row2['IntersectionID']==interID:
						cycle=int(row2['CycleTime'])

			ratio=float(greentime)/float(cycle)
			s=row['GreenLinkID']
			#print s
			news=s.split("_")
			#print news
			for each in news:
				if each =="":
					continue
				linkId= int(each)

				for index3,row3 in linkTable.iterrows():

					if int(row3['linkID'])==linkId:
						linkTable.set_value(index3,['linkgreensplit'],ratio)
		return True
	
	def costfunction(self,chromosome,phaseTable,linkTable,intersectionTable):
		if len(chromosome)==len(phaseTable.index):
			#print ("good")
			for i,row in phaseTable.iterrows():
				phaseTable.set_value(i,['PhaseDuration'],chromosome[i])
		else:
			print ("chromosome and phaseTable have different number of rows!")
			print ((chromosome))
			print (len(phaseTable.index))

		#get link split time in linkTable
		self.getlinkGreenSplit(linkTable,phaseTable,intersectionTable)
		
		#get BPR cost
		self.BPRcost(linkTable,0.15,4)
		totalcost=0
		for i,row in linkTable.iterrows():
			totalcost=totalcost+row['cost']
		#print(totalcost)
		return totalcost

	def updateSignals(self,chromosome,phaseTable):
		if len(chromosome)==len(phaseTable.index):
			#print ("good")
			for i,row in phaseTable.iterrows():
				#phaseTable.set_value(i,['PhaseDuration'],chromosome[i])
				phaseTable.at[i,'PhaseDuration']=chromosome[i]
		else:
			print ("chromosome and phaseTable have different number of rows!")
			print ((chromosome))
			print (len(phaseTable.index))
		control_plan=model.getCatalog().find(1068)

		for index,row in phaseTable.iterrows():
			greentime =int(row['PhaseDuration'])
			phaseID=int(row['PhaseID'])
			interID=int(row['IntersectionID'])
			junctionNode=model.getCatalog().find(interID)
			controljunction=control_plan.getControlJunction(junctionNode)
			if controljunction ==None:
				print ("Error in finding current node in control plan!")
			myphases=controljunction.getPhases()
			if (phaseID-1)==0:
				entry=0
			#print (phaseID-1)
			phase=myphases[phaseID-1]	
			#print "entry="+str(entry)
			#print "green="+ str(greentime)
			phase.setFrom(entry)
			phase.setDuration(greentime)
			entry+=greentime


	def update_link_green_split_AIMSUN(self):
		# set all section UserDefinedCost into 1
		type = model.getType("GKSection")
		for section in GK.GetObjectsOfType(type):
				if section.getUserDefinedCost()!=1.0:
					section.setUserDefinedCost(1.0)
				if section.getUserDefinedCost2()!=0.0:
					section.setUserDefinedCost2(0.0)
		# get each signalized signals in a control plan

		control_plan=model.getCatalog().find(1068)

		junctions=control_plan.getControlJunctions()
		for junction in junctions:
			#print junction
			junctionNode=model.getCatalog().find(junction)
			controljunction=control_plan.getControlJunction(junctionNode)
			cycle=controljunction.getCycle()
			phases=controljunction.getPhases()
			
			#signalgroups=junctionNode.getSignals()
			allturnings=junctionNode.getTurnings()
			for each_phase in phases:
				duration=each_phase.getDuration()
				#print duration	

				#for each_signal_group in signalgroups:
					#if each_phase.findSignal(each_signal_group.getId()) == 1:#? 
						#print str("this phase consist:"+each_signal_group.getName())
						#turnings=each_signal_group.getTurnings()
						#for eachturning in turnings:
							#myoriginsection=eachturning.getOrigin()
							#green_split=float(duration/cycle)+myoriginsection.getUserDefinedCost2()
							#myoriginsection.setUserDefinedCost2(myoriginsection.getUserDefinedCost2()+duration/cycle)
				for each_turning in allturnings:
					if each_phase.turningHasGreen(each_turning)==1:
						#print str("this phase consist turining:"+str(each_turning.getId()))
						myoriginsection=each_turning.getOrigin()
						green_split=float(duration/cycle)+myoriginsection.getUserDefinedCost2()
						if myoriginsection.getUserDefinedCost()==1.0:
							myoriginsection.setUserDefinedCost(float(duration/cycle))
						else:
							myoriginsection.setUserDefinedCost(myoriginsection.getUserDefinedCost()+duration/cycle)
		#print "done!"
	def returnColumnsForOriginator(self,originator, objectType):
		listColumns = []
		columns = objectType.getColumns(GKType.eSearchThisAndParentTypes)
		countColumns = 0

		for column in columns:
			countColumns = countColumns + 1

			columnOriginator = column.getOriginator()
			localType = column.getType()

			if columnOriginator == originator:
				listColumns.append(column)
		return listColumns
	def get_simulated_cost1(self):
		totalcost=0
		target=model.getCatalog().find(1050)

		GKSystem.getSystem().executeAction( "execute", target, [], ""  )#run assignment
		statsManager = target.getStatsManager()
		sections = statsManager.getSections()
		turnings = statsManager.getTurnings()
		users = statsManager.getUserIds() #car types
		iterationInfo = statsManager.getIterationsInfo()
		for user in users:
			totalcost+=statsManager.getTotalCost(user)			
		return totalcost
	def get_simulated_cost2(self): #total delay time

		target=model.getCatalog().find(1177)

		GKSystem.getSystem().executeAction( "execute", target, [], ""  )#run assignment
		objectTP=model.getType("GKReplication")
		columns=self.returnColumnsForOriginator(target,objectTP)
		for colum in columns:
			if colum.getName()=="DYNAMIC::SRC_GKReplication_delayTime_0":
				#"DYNAMIC::GKReplication_totalTravelTimeInside_1177_0" 
				#"DYNAMIC::SRC_GKReplication_totalWaitingTime_0"
				resultTimeSeries = target.getDataValueTS(colum)
				#print colum.getName()
				resultDescription = resultTimeSeries.getDescription()
				resultFromDateTime = resultDescription.getFromTime()
				#print resultFromDateTime
				resultToDateTime = resultDescription.getToTime()
				#print resultToDateTime
				
				#currentTimeSlice = resultFromTime
				NumberOfInterval = resultDescription.getInterval(resultToDateTime)+1
				total_delayTime=0
				for i in range(NumberOfInterval):
					resultIndex=GKTimeSerieIndex(i)
					resultValue =  resultTimeSeries.getValue(resultIndex)
					total_delayTime+=float(resultValue[0])
					#print str(len(resultValue))+ "!!!!" + str(resultValue[0])+"!!!!" + str(resultValue[1])
				agreggated_delay=total_delayTime/float(NumberOfInterval)
				print (agreggated_delay)
				break
		return agreggated_delay

	def get_simulated_cost(self):#total travel time

		target=model.getCatalog().find(1177)

		GKSystem.getSystem().executeAction( "execute", target, [], ""  )#run assignment
		objectTP=model.getType("GKReplication")
		columns=self.returnColumnsForOriginator(target,objectTP)
		totaltraveltime=0
		for colum in columns:
			if colum.getName()=="DYNAMIC::GKReplication_totalTravelTimeInside_1177_0" :
				resultTimeSeries = target.getDataValueTS(colum)
				resultDescription = resultTimeSeries.getDescription()
				resultFromDateTime = resultDescription.getFromTime()
				resultToDateTime = resultDescription.getToTime()
				LastintervalID = resultDescription.getInterval(resultToDateTime)
				resultIndex=GKTimeSerieIndex(LastintervalID)
				resultValue =  resultTimeSeries.getValue(resultIndex)
				totaltraveltime+=float(resultValue[0])
			if colum.getName()=="DYNAMIC::SRC_GKReplication_totalWaitingTime_0" :
				resultTimeSeries = target.getDataValueTS(colum)
				resultDescription = resultTimeSeries.getDescription()
				resultFromDateTime = resultDescription.getFromTime()
				resultToDateTime = resultDescription.getToTime()
				LastintervalID = resultDescription.getInterval(resultToDateTime)
				resultIndex=GKTimeSerieIndex(LastintervalID)
				resultValue =  resultTimeSeries.getValue(resultIndex)
				totaltraveltime+=float(resultValue[0])
				
		return totaltraveltime
   

 
#new ML predicting cost function (choose the first chromosome as the observed section status)

	def get_ML_predicted_cost1(self,chromo):
		#get one line from dataframe:
		#print (X_df.head())    
		allcolumns=X_df.columns
		myx=(X_df.iloc[0])    
		#print (myx)
		#print (len(chromo))
    
		for i in range(len(chromo)):
			columnname='p'+str(i+1)
			#print (myx[columnname])
			#print (chromo[i])
			myx[columnname]=chromo[i]

		myx=(pd.DataFrame(myx))
		#print (myx)
    
    
		#transfer the dataframe into an array
    
		myxarraylist=[]#myx.values

		for i in myx.values:
			#print(i[0])
			a=i[0]
			myxarraylist.append(a)
		myxarraylist=np.array(myxarraylist)
		myxarraylist=[myxarraylist]
		#print(myxarraylist)

		#print([X_test[0]])
		totalcost=bestregressor.predict(myxarraylist)

        
		return totalcost
#new ML predicting cost function (choose the best chromosome as the observed section status)
	def get_ML_predicted_cost(self,chromo):
		#get one line from dataframe:
		#print (X_df.head())    
		allcolumns=X_df.columns
		mindex=np.where(y == np.amin(y))
		#print(mindex[0][0])    
		myx=(X_df.iloc[mindex[0][0]])

		print (myx)
		#print (len(chromo))
    
		for i in range(len(chromo)):
			columnname='p'+str(i+1)
			#print (myx[columnname])
			#print (chromo[i])
			myx[columnname]=chromo[i]

		myx=(pd.DataFrame(myx))
		#print (myx)
    
    
		#transfer the dataframe into an array
    
		myxarraylist=[]#myx.values

		for i in myx.values:
			#print(i[0])
			a=i[0]
			myxarraylist.append(a)
		myxarraylist=np.array(myxarraylist)
		myxarraylist=[myxarraylist]
		#print(myxarraylist)

		#print([X_test[0]])
		totalcost=(bestregressor.predict(myxarraylist))
		if totalcost<0:
			totalcost=999
        
		return totalcost 

	def BPRcost(self,each,a,b):
		each['cost']= each['length']/each['speedlimit']*(1+a*(each['flow']/each['capacity']/each['linkgreensplit'])**b)
		pass

In [14]:
#global parameters
steplength=1 #step length for mutation action
noEpisode=100 #policy generating episode
numberOfActions=4*(4-1)**4
print (numberOfActions)
intersectionTB=Table1
phaseTB=Table2
linkTB=Table3
filefullpath=folder_path
def return_action_id(intID,pid1,pid2):
	if 1:
		linecounter=0
		newchromosome=list()
		for index,row in intersectionTB.iterrows():
			subchromo=list()
			myintID=row['IntersectionID']
			numofphases=row['NumOfPhase']
			for i in range(numofphases):
				for j in  range(numofphases):
					if myintID==intID and i==pid1 and j==pid2:
						return linecounter
					if i!=j:
						linecounter+=1
	return -1
def fromID_to_action(mID):
	linecounter=0
	for index,row in intersectionTB.iterrows():
			subchromo=list()
			myintID=row['IntersectionID']
			numofphases=row['NumOfPhase']
			for i in range(numofphases):
				for j in  range(numofphases):
					if linecounter==mID:
						return myintID,i,j
					if i!=j:
						linecounter+=1
	return -1
def generate_policy_naive_reward_agent(num_episodes=1):
	r_table=pd.DataFrame({"state":[],"action":[]})
	r_table.columns = ['state', 'action']
	print (r_table)
	s=OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=25,size=75,filepointer=filefullpath,prob_mutation=0.1,prob_crossover=0.9).random_chromo(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3)
	pre_fitness=0#OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=25,size=75,filepointer=filefullpath,prob_mutation=0.1,prob_crossover=0.9).fitness(chromo=s,intersectionTB=Table1,phaseTB=Table2,linkTB=Table3)
	print (s)
	mutation_limit=100
	for g in range(num_episodes):
		done=False
		mutation_count=0
		print (r_table.count)
		while not done:
			#if str(s) not in r_table.keys():
			if r_table.empty:
				actionarray=[0] * (numberOfActions)#initialization
				#print actionarray
				newchrome=[]
				print ("111")
				intID,pid1,pid2,newchrome=OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=25,size=75,filepointer=filefullpath,prob_mutation=0.1,prob_crossover=0.9).mutation_action_record(s)
				print (intID)
				print (pid1)
				print (pid2)
				print (newchrome)
				after_fitness=OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=25,size=75,filepointer=filefullpath,prob_mutation=0.1,prob_crossover=0.9).fitness(chromo=newchrome,intersectionTB=Table1,phaseTB=Table2,linkTB=Table3)
				reword=after_fitness-pre_fitness
				print (after_fitness)
				print (pre_fitness)
				print (return_action_id(intID,pid1,pid2))
				actionarray[return_action_id(intID,pid1,pid2)]+=float(reword)
				print (actionarray[return_action_id(intID,pid1,pid2)])
				############canniot use chromosome as dictionary keys
				print (len(s))
				print (len(actionarray))
				
				r_table=pd.DataFrame({"state":str([s]),"action":[actionarray]})
				
				s=newchrome
				print ([s])
				print (r_table.loc[r_table['state']==str([s])])
				pre_fitness=after_fitness
				mutation_count+=1
				print ("!!!")
			elif  r_table.loc[r_table['state']==str([s])].empty:
				actionarray=[0] * (numberOfActions)#initialization
				#print actionarray
				newchrome=[]
				print ("111")
				intID,pid1,pid2,newchrome=OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=25,size=75,filepointer=filefullpath,prob_mutation=0.1,prob_crossover=0.9).mutation_action_record(s)
				print (intID)
				print (pid1)
				print (pid2)
				print (newchrome)
				after_fitness=OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=25,size=75,filepointer=filefullpath,prob_mutation=0.1,prob_crossover=0.9).fitness(chromo=newchrome,intersectionTB=Table1,phaseTB=Table2,linkTB=Table3)
				reword=after_fitness-pre_fitness
				print (after_fitness)
				print (pre_fitness)
				print (return_action_id(intID,pid1,pid2))
				actionarray[return_action_id(intID,pid1,pid2)]+=float(reword)
				print (actionarray[return_action_id(intID,pid1,pid2)])
				############canniot use chromosome as dictionary keys
				print (len(s))
				print (len(actionarray))
				################python error()!
				#r_table.append([s,actionarray])
				new_line=pd.DataFrame({"state":str([s]),"action":[actionarray]})
				print (new_line["state"])
				r_table=r_table.append([new_line],ignore_index=True)
				print (r_table)
				#row=pd.DataFrame([[s]],[[actionarray]], columns={'state','action'})
				#r_table.append(row)
				
				#r_table.append(row)
				s=newchrome
				pre_fitness=after_fitness
				mutation_count+=1
				print ("???")
			else:
				new1=r_table.loc[r_table["state"]==str([s]),['action']]
				index=r_table.loc[r_table["state"]==str([s]),['action']].index[0]
				print (index)
				print ("?!?")
				###actionarray is string now,need to transfer into array
				new2=new1.reset_index()
				print ("ccc")
				print (new2.count)
				if new2['action'].count()>1:
					print ("more than one line observed with same state")
				elif new2['action'].count()==1:
					actionarray=new2.at[0,'action']
				else:
					print ("wtf")
				print (actionarray)
				print ("wc")
				###now the actionarray is now an array
				intID,pid1,pid2,newchrome=OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=25,size=75,filepointer=filefullpath,prob_mutation=0.1,prob_crossover=0.9).mutation_action_record(s)
				while actionarray[return_action_id(intID,pid1,pid2)]!=0:
					intID,pid1,pid2,newchrome=OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=25,size=75,filepointer=filefullpath,prob_mutation=0.1,prob_crossover=0.9).mutation_action_record(s)
				print ("333")
				after_fitness=OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=25,size=75,filepointer=filefullpath,prob_mutation=0.1,prob_crossover=0.9).fitness(chromo=newchrome,intersectionTB=Table1,phaseTB=Table2,linkTB=Table3)
				reword=after_fitness-pre_fitness
				actionarray[return_action_id(intID,pid1,pid2)]+=reword
				print("444")
				##########################
				r_table.at[index,'action']=actionarray
				s=newchrome
				pre_fitness=after_fitness
				mutation_count+=1
			if mutation_count>=mutation_limit:
				done=True
			#break
	#print actionarray
	print_r_table(r_table)
	print ("555")
	#break
	################output the r_table


def print_r_table(r_tb):
	file_path=osp.join(folder_path,"r_table.txt")
	r_tb.to_csv(file_path)
	
def read_r_table():
	file_path=osp.join(folder_path,"r_table.txt")
	return pd.read_csv(file_path)


#generate_policy_naive_reward_agent()
#mytb=read_r_table()
#print mytb
#one experiment
import time
start_time=time.ctime()
filename="GAoutput.csv"
filefullpath=osp.join(folder_path, filename)
#print "111"
file = open(filefullpath, "a")
file.write("started at %s\n"%str(start_time))
file.write("GenerationID,MaxFitness,MinFitness,Mean,STD,time\n")
file.close()
#print "222"
a=OptimizeSignal(intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,limit=20,size=75,filepointer=filefullpath,prob_mutation=0.2,prob_crossover=0.9).run(Table1,Table2,Table3)#self, target_phasetime=[1,2,3,84],intersectionTB=Table1,phaseTB=Table2,linkTB=Table3,imit=100, size=500,prob_crossover=0.9, prob_mutation=0.2
end_time=time.ctime()
file2 = open(filefullpath, "a")
file2.write("finish at"+str(end_time)+"\n")
file2.close()
print (start_time)
print (end_time)
#print return_action_id(1328,0,1)
print ("done")

324
[15, 25, 42, 8, 88, 0, 0, 2, 41, 7, 7, 35, 4, 10, 49, 27]
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200

D:\Anaconda\lib\site-packages\ipykernel_launcher.py:651: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


[78, 11, 1, 0, 7, 43, 35, 5, 9, 57, 13, 11, 25, 7, 45, 13]
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200_sp

[19, 10, 29, 32, 50, 17, 22, 1, 64, 19, 0, 7, 68, 11, 4, 7]
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200_s

[77, 9, 2, 2, 47, 15, 2, 26, 89, 1, 0, 0, 7, 63, 6, 14]
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200_speed

...

[34, 11, 8, 37, 8, 20, 16, 46, 37, 12, 2, 39, 23, 6, 12, 49]
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200_

[35, 4, 5, 46, 15, 10, 16, 49, 74, 12, 2, 2, 10, 5, 27, 48]
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200_s

[32, 15, 6, 37, 8, 18, 14, 50, 37, 10, 1, 42, 23, 6, 11, 50]
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200_

[28, 3, 15, 44, 5, 21, 16, 48, 15, 9, 2, 64, 29, 6, 3, 52]
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200_sp

[38, 14, 5, 33, 5, 18, 12, 55, 31, 11, 8, 40, 19, 6, 18, 47]
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200_

In [15]:
y

array([6906, 6018, 6143, ..., 3862, 3518, 3516], dtype=int64)

In [16]:
[73, 13, 0, 4, 10, 44, 20, 16, 90, 0, 0, 0, 83, 0, 7, 0]
def get_ML_predicted_cost(chromo):
	#get one line from dataframe:
	#print (X_df.head())    
	allcolumns=X_df.columns
	mindex=np.where(y == np.amin(y))
	print(mindex[0][0])    
	myx=(X_df.iloc[mindex[0][0]])

	print (myx)
	#print (len(chromo))
    
	for i in range(len(chromo)):
		columnname='p'+str(i+1)
		#print (myx[columnname])
		#print (chromo[i])
		myx[columnname]=chromo[i]

	myx=(pd.DataFrame(myx))
	#print (myx)
    
    
	#transfer the dataframe into an array
    
	myxarraylist=[]#myx.values

	for i in myx.values:
		#print(i[0])
		a=i[0]
		myxarraylist.append(a)
	myxarraylist=np.array(myxarraylist)
	myxarraylist=[myxarraylist]
	print(myxarraylist)

	print([X_test[0]])
	totalcost=bestregressor.predict(myxarraylist)

        
	return totalcost
get_ML_predicted_cost([73, 13, 0, 4, 10, 44, 20, 16, 90, 0, 0, 0, 83, 0, 7, 5])

1060
0_section_1190_flow       462.00
0_section_1190_speed       22.16
0_section_1190_density     67.93
0_section_1191_flow       120.00
0_section_1191_speed       54.97
0_section_1191_density      1.10
0_section_1192_flow        90.00
0_section_1192_speed       53.28
0_section_1192_density    131.10
0_section_1193_flow       468.00
0_section_1193_speed       52.86
0_section_1193_density      4.45
0_section_1194_flow       348.00
0_section_1194_speed       48.75
0_section_1194_density      3.94
0_section_1195_flow        90.00
0_section_1195_speed       49.64
0_section_1195_density     36.24
0_section_1196_flow       258.00
0_section_1196_speed       50.11
0_section_1196_density      7.07
0_section_1197_flow       426.00
0_section_1197_speed       52.54
0_section_1197_density     52.06
0_section_1198_flow       732.00
0_section_1198_speed       53.54
0_section_1198_density     12.80
0_section_1200_flow       222.00
0_section_1200_speed       53.76
0_section_1200_density      2.07
     

D:\Anaconda\lib\site-packages\ipykernel_launcher.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


[array([ 4.6200e+02,  2.2160e+01,  6.7930e+01,  1.2000e+02,  5.4970e+01,
        1.1000e+00,  9.0000e+01,  5.3280e+01,  1.3110e+02,  4.6800e+02,
        5.2860e+01,  4.4500e+00,  3.4800e+02,  4.8750e+01,  3.9400e+00,
        9.0000e+01,  4.9640e+01,  3.6240e+01,  2.5800e+02,  5.0110e+01,
        7.0700e+00,  4.2600e+02,  5.2540e+01,  5.2060e+01,  7.3200e+02,
        5.3540e+01,  1.2800e+01,  2.2200e+02,  5.3760e+01,  2.0700e+00,
        9.6000e+01,  5.3820e+01,  1.1988e+02,  2.2800e+02,  5.4380e+01,
        2.1000e+00,  1.9200e+02,  5.4320e+01,  1.7800e+00,  5.1000e+02,
        5.2900e+01,  3.6640e+01,  1.2000e+02,  5.2090e+01,  1.1600e+00,
        7.8000e+01,  4.2090e+01,  1.1160e+02,  6.0000e+01,  5.4400e+01,
        5.6000e-01,  9.9600e+02,  3.8020e+01,  8.4460e+01,  3.3000e+02,
        2.5320e+01,  1.1724e+02,  1.7400e+02,  5.3900e+01,  1.6200e+00,
        2.6400e+02,  5.5790e+01,  2.3800e+00,  3.0000e+02,  5.1900e+01,
        7.6100e+01,  3.1800e+02,  5.4370e+01,  7.5490e+01,  3.6

array([222.40456], dtype=float32)